## LangChain 사용해서 지원사업 공고 파일(pdf, hwp, png)을 요약해보자!

In [1]:
from openai import OpenAI
from getpass import getpass
from tqdm import tqdm

from utils.get_text import get_hwp_text, get_pdf_text, get_image_text # pdf, hwp, img에서 텍스트를 추출하는 사용자 지정 함수 

- LangChain 모델이 참고할 비슷한 용어 사전
- 개발팀이 직접 정의
- (추후에 유사한 단어가 나오면 사전에 추가하는 기능도 구현할 예정)

In [2]:
# 정의한 비슷한 용어 사전
keyword_dictionary = {  
                        '사업자 유형' : ['개인사업자', '법인사업자', '창업(예비사업자 포함)', '재창업', '기존사업자'],
                        '지원업종' : ['자동차 및 부품 판매업','도매 및 상품 중개업','소매업(자동차 제외)','숙박업', '음식점업', '제조업','교육 서비스업', '협회 및 단체, 수리 및 기타 개인 서비스업','부동산업','전문, 과학 및 기술 서비스업','예술, 스포츠 및 여가관련 서비스업','정보통신업','농업, 임업 및 어업','건설업','운수 및 창고업','보건업 및 사회복지 서비스업','사업시설 관리, 사업 지원 및 임대 서비스업','금융 및 보험업','전기, 가스, 증기 및 공기 조절 공급업','광업','수도, 하수 및 폐기물 처리, 원료 재생업','가구 내 고용활동 및 달리 분류되지 않은 자가 소비 생산활동','공공행정, 국방 및 사회보장 행정','국제 및 외국기관'],
                        '정보통신업' : ['정보통신 서비스업', '정보통신기기 제조업', '소프트웨어 및 컴퓨터 관련 서비스업'],
                        '공고 특성' : ['청년 대상', '여성 대상', '소상공인', '대출', '마케팅·홍보', '보조금', '폐업', '고용지원', '시설·환경 개선', '입주·임대 지원', '희망리턴패키지', '고용유지지원금', '희망대출플러스', '두루누리지원금', '창업패키지', '노란우산공제', '이커머스 입점피해'],
                        '창업패키지' : ['예비창업패키지', '초기창업패키지', '청년창업사관학교'],
                        '신청기간' : ['신청 기간', '접수 기간', '자금 소진시까지'],
                        '신청방법' : ['지원 대상', '사업 대상', '융자 대상', '접수방법','접수'],
                        '지원제외' : ['지원 제외','지원 취소', '제외 대상', '제한 대상'],
                        '우대사항' : ['벤처기업', '여성기업', '사회적기업(인증)', '장애인기업', '이노비즈제도','메인비즈제도','가족친화인증기업', '수출유망중소기업','녹색기술인증기업','내일채움공제 가입기업','글로벌 강소기업', '기술혁신중소기업'],
                        '유의사항' : ['의무사항', '지원 취소 및 제외', '기타 안내사항'],
                        '제출 서류' : ['필요 서류', '서류 제출 목록'],
                        '선정 절차' : ['선정 절차', '평가 방법', '평가 방향', '우대 사항', '평가 방향', '선정 기준', '지원 절차'],
                        '지원 내용' : ['지원 내용', '규모', '분야 및 대상', '범위 및 형태', '세부지원내용', '지원조건'],
                        '문의처' : ['문의 전화', '연락처', '지원 문의처', '문의 및 상담', '접수 및 문의', '접수'],
                        '기타' : ['기타']
                        }

#### model 구현 준비
- OpenAI 객체 생성
- 파일 텍스트 추출
- model이 참고할 기본 템플릿 작성

In [3]:
# 개인의 API key를 입력
MY_API_KEY = getpass("OpenAI API Key")

#OpenAI 객체 생성
client = OpenAI(api_key=MY_API_KEY)

In [4]:
# 파일 경로 설정 (백슬래시 문제 해결을 위해 r"" 사용)
file_path = f"금융/[경기] 부천시 2025년 소상공인 특례보증ㆍ이차보전 지원계획 공고.pdf"

# 지원사업명 저장 (지원경로를 분할하여 사용)
title = file_path.split('/')[1].split('.')[0]

# 파일 타입 저장 (지원경로를 분할하여 사용)
file_type = file_path.split('/')[1].split('.')[1]

# file_type이 pdf면 get_pdf_text, hwp면 get_hwp_text를 사용하여 텍스트 추출
if file_type == 'pdf':
    full_text = get_pdf_text(file_path)
elif file_type == 'hwp':
    full_text = get_hwp_text(file_path)

In [9]:
base_template = {f'''
📌 {title} 요약 안내

✅ 사업자 유형

☑️ 지원업종

💡 공고특성

👥 지원대상

📅 신청기간

📝 신청방법 

🚫 지원제외 대상

⭐️ 우대사항

👩 여성 대상

💁 청년 대상

⚠ 유의사항  

📑 제출서류  

📌 선정절차  

💰 지원내용  

📞 문의처

'''
}

# 📢 **기타 안내**  

In [6]:
explanation = {f'''
- 중소기업은 중소기업기본법에 정의된 기준을 따르며 개인사업자, 법인사업자, 기존사업자를 포함해주세요.
- 시설·환경 개선 자금은 기업 운영에 필요한 기계설비, 공장설립, 토지구입 등에 사용되는 자금, 원자재 구매, 생산, 판매 등 기업의 운영에 필요한 자금입니다.
- 청년은 만 19세 이상 39세 이하를 의미합니다. 
- 전용 대상은 특정 대상만 신청이 가능한 경우를 의미하고, 우대 조건은 특정 대상에게 가점을 부여하는 경우를 의미합니다.
- 공고에서 언급된 모든 금리 우대 항목을 추출해주세요. 
- 여성대상과 청년대상은 대상이 여성만 또는 청년만 되는 내용이 있는 경우에 해당하며 O,X로 구분해주세요.
- 만약 '변동없음'이라고 기재되어 있다면, 기존에 제공된 값을 찾아서 사용하세요. 즉, 당초(1,3,5,6,9월)이라면 기존 값을 그대로 추출하세요.
'''}

#### LangChain 모델로 간단하게 요약해보기
- (고도화 예정)

In [10]:
from langchain_openai import ChatOpenAI
from langchain_core.prompts import PromptTemplate
from langchain_core.output_parsers import StrOutputParser

template = """
당신은 정부 지원 사업 전문 분석가입니다. 

사용자가 요구하는 파일을 제공하는 템플릿 양식에 맞게 추출해야합니다. 파일 내용을 철저하게 분석하고, 어떤 항목도 누락시키지 마세요. 파일에 없는 내용은 공백으로 남겨두십시오.
요구하는 파일은 양식이 일정하지 않습니다. 정의된 사전을 선언해두었으니 사전에 해당하는 단어가 나오면 참고해주십시오.

사업자 유형, 지원업종, 공고특성, 우대사항 항목은 문맥을 분석해 가장 적합한 단어를 단어사전 내에서 선택해주세요.조건에 해당하는 사항이 중복되는 경우, 각 대상에 모두 포함시켜주세요.
다른 항목의 경우는 사전에 해당하지 않는 단어가 나오면, 해당 단어를 그대로 사용하여 요약해주십시오.

신청기간과 제출서류는 각 항목을 세분화할 수 있는 경우, 세분화하여 요약해주세요.

지원대상, 신청방법은 모든 내용을 누락없이 추출해주세요. 접수처와 접수처 현황까지 모두 포함해야 합니다.
신청기간과 제출서류가 자금마다 두 가지 이상으로 다르게 제시된 경우에만 '공고문 참조'로 대체해주세요. 만약 신청기간이나 제출서류가 하나로 통일되어 있거나, 하나의 기간 혹은 제출서류만 존재하는 경우에는 구체적인 값을 출력해주세요.

신청방법, 지원내용 항목의 경우 표로 제시된 정보는 그대로 표 형태로 출력해주세요. 표는 데이터프레임 형식으로 출력해주세요.

제공하는 템플릿 양식 : {base_template}
단어 정의 사전 : {keyword_dictionary}
참고 : {explanation}
---------------------------------------------------
사용자 요구 파일 : {text}

각 항목의 범위를 명확히 구분하고, 잘못 분류된 정보를 수정해주세요.
"""

# 파일 요약을 위한 프롬프트 템플릿을 정의
prompt = PromptTemplate.from_template(template)

# OpenAI의 GPT-4o 모델을 사용하여 채팅 모델을 생성
model = ChatOpenAI(
    model='gpt-4o',  # 사용할 언어 모델 지정
    api_key=MY_API_KEY,  # OpenAI API 키 입력
    temperature=0
)

# 모델의 출력을 문자열로 변환하는 출력 파서
output_parser = StrOutputParser()

# 체인(Chain) 구성: 프롬프트 → 모델 → 출력 파서 순서로 연결
chain = prompt | model | output_parser

In [12]:
summary = chain.invoke({'base_template':base_template,
              'keyword_dictionary':keyword_dictionary,
                'explanation': explanation,
              'text':full_text})

In [15]:
summary

'```\n📌 [경기] 부천시 2025년 소상공인 특례보증ㆍ이차보전 지원계획 공고 요약 안내\n\n✅ 사업자 유형\n- 소상공인\n- 기존사업자\n\n☑️ 지원업종\n- 소매업(자동차 제외)\n- 도매 및 상품 중개업\n- 음식점업\n- 제조업\n- 기타 서비스업\n\n💡 공고특성\n- 소상공인\n- 대출\n\n👥 지원대상\n- 부천시 소재 소상공인\n- 사업자 등록일로부터 2개월 이상 경과된 사업자\n\n📅 신청기간\n- 상반기: 2025. 1. 23. ~ 자금소진시까지\n- 하반기: 2025. 7. 1. ~ 자금소진시까지\n\n📝 신청방법\n| 구분     | 내용                                                                 |\n|----------|----------------------------------------------------------------------|\n| 접수처   | 경기신용보증재단 부천지점                                           |\n| 연락처   | 1577-5900                                                            |\n| 주소     | 부천시 원미구 소향로 217, 4층                                       |\n| 준비서류 | 사업자등록증 사본, 매출증빙서류, 신분증 등                           |\n\n🚫 지원제외 대상\n- 지방세, 세외수입 등 체납이 있는 사업자\n- 제한업종(금융업, 유흥업, 불법도박 및 사치, 향락업종 등)\n\n⭐️ 우대사항\n- \n\n👩 여성 대상\n- X\n\n💁 청년 대상\n- X\n\n⚠ 유의사항\n- 사업장 휴․폐업, 사업장 타 시․군 이전 시 지원 중지 및 환수\n\n📑 제출서류\n- 사업자등록증 사본\n- 매출증빙서류\n- 신분증 등\n\n📌 선정절차\n- 상담․접수 ➡ 심사(서류․

## 기존 json 파일에 요약 추가해보기

In [17]:
import json

In [18]:
with open('data/final_Vector.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

In [26]:
for idx in tqdm(data['금융'][:10]):

    vector_path = idx['공고파일명']
    
    # 지원사업 텍스트 추출 (PDF/HWP 처리 함수 필요)
    if vector_path.endswith("pdf"):
        full_text = get_pdf_text(vector_path)
    elif vector_path.endswith("hwp"):
        full_text = get_hwp_text(vector_path)
    elif vector_path.endswith("png"):
        full_text = get_image_text(vector_path)

    summary = chain.invoke({'base_template':base_template,
              'keyword_dictionary':keyword_dictionary,
                'explanation': explanation,
              'text':full_text})
    
    idx['summary'] = summary

100%|██████████| 10/10 [01:12<00:00,  7.27s/it]


In [28]:
data

{'금융': [{'지원사업 공고명': '[인천] 2025년 소공인 지원 특례보증 사업 공고(소공인 경영안정 및 성장지원)',
   '소관부처·지자체': '인천광역시',
   '사업수행기관': '인천신용보증재단',
   '신청기간': '예산 소진시까지',
   '공고파일명': '금융/[인천] 2025년 소공인 지원 특례보증 사업 공고(소공인 경영안정 및 성장지원).hwp',
   'vector': [0.004528796300292015,
    0.013785794377326965,
    -0.0047311498783528805,
    -0.01883022114634514,
    0.032744113355875015,
    -0.02906889095902443,
    -0.038783181458711624,
    0.07865076512098312,
    0.039984434843063354,
    -0.009734414517879486,
    0.03644763305783272,
    -0.011030763387680054,
    -0.02750898152589798,
    0.022832082584500313,
    -0.025479676201939583,
    -0.014244487509131432,
    -0.027050776407122612,
    0.039871349930763245,
    -0.000700047763530165,
    -0.015361003577709198,
    0.01658090017735958,
    -0.01963888294994831,
    -0.02975410409271717,
    -0.013005122542381287,
    -0.02614406868815422,
    -0.02776985988020897,
    0.011519497260451317,
    -0.04676172882318497,
    -0.007562022190541029,
    -0.0527559407

In [29]:
with open('data/streamlit_test.json', 'w', encoding='utf-8') as f:
    json.dump(data, f, ensure_ascii=False, indent=4)


In [38]:
with open('data/streamlit_test.json', 'r', encoding='utf-8') as f: # 파일 저장되어 있는 위치 수정할것
    data = json.load(f)

test_data = data['금융'][:10]
test_data[2]['summary'] # test_data[0]~[9] 까지의 data만 존재

'```\n📌 [광주] 2025년 중소사업장 가족친화경영 지원사업 공고 요약 안내\n\n✅ 사업자 유형\n중소사업장\n\n☑️ 지원업종\n공공행정, 국방 및 사회보장 행정\n\n💡 공고특성\n가족친화경영, 지원금\n\n👥 지원대상\n광주광역시 관내 근로자 5인 이상 300인 미만 고용보험 가입 가족친화경영 실천 중소사업장\n\n📅 신청기간\n2025. 3. 26.(13:00) ~ 4. 2.(18:00)\n\n📝 신청방법\n| 접수처 | 방법 |\n|--------|------|\n| 광주광역시 일가정양립지원본부 직장맘지원팀 | 전자우편(n8306110@korea.kr) 제출 |\n\n🚫 지원제외 대상\n- 2020년 ~ 2024년 가족친화경영 지원사업 수혜기업 (단, 가족친화 선도기업 1회에 한하여 재지원 가능)\n- 국세지방세 등 체납중인 업체\n- 대기업, 공공기관, 공사공단\n- 비영리법인, 사단법인, 민간단체위탁기관, 교육기관 등\n\n⭐️ 우대사항\n가족친화인증기업\n\n👩 여성 대상\nX\n\n💁 청년 대상\nX\n\n⚠ 유의사항\n- 서류제출은 `25.3.26.(13:00) ~ 4.2.(18:00) 도착분까지 유효합니다.\n- 접수된 서류는 반환하지 않습니다.\n- 접수된 서류 중 사실과 다른 내용의 서류를 제출하거나 허위를 기재할 시에는 무효로 처리됩니다.\n- 제출된 서류는 추후 가족친화경영 홍보를 위해 자료로 사용될 수 있습니다.\n- 본 사업은 가족친화 기업문화조성을 위해 광주광역시가 운영하는 자체사업으로 여성가족부 가족친화인증 지표를 참조하고 있습니다.\n- 가족친화경영지원금은 사업주가 수혜대상이 될 수 없습니다.\n\n📑 제출서류\n- 신청서(서식 1~4/체크리스트 포함) 각 1부 (기본 파일의 서식변경 금지)\n- 사업자등록증 및 4대보험사업장가입자명부(남녀구분), 국세지방세 납세증명서 각 1부\n- 가족친화인증기업 인증서 제출 (해당기업)\n- 남성 육아휴직 실적 기업-고용노동부 육아휴직 확인서(23년~25년 이내) 1부(해당기업)\

In [34]:
test_data = data['금융'][:10]

In [36]:
test_data[0]['summary']

'```\n📌 [인천] 2025년 인천광역시 소공인 지원 특례보증 사업공고 요약 안내\n\n✅ 사업자 유형\n소상공인\n\n☑️ 지원업종\n제조업\n\n💡 공고특성\n소상공인, 대출\n\n👥 지원대상\n인천광역시 소재 상시 근로자 10인 미만으로 제조업을 영위하고 있는 소공인(소공인기본법 제2조에 따른 소공인)\n\n📅 신청기간\n2025. 3. 19.(수) 오전 9시 ~ 자금 소진시까지\n\n📝 신청방법\n| 신청방법 | 비고 |\n|----------|------|\n| 온라인 예약 | 보증드림App 접속 후 보증신청하기 클릭 > 본상품 선택한 후에 비대면상담 예약 절차 진행 |\n| 지점 방문 | 디지털 소외계층에 한함, 사업장 주소지 관할 지점으로만 가능 |\n\n🚫 지원제외 대상\n- 최근 3개월 이내에 재단의 신규보증을 지원받은 기업\n- 과거 동일한 특례보증을 기 지원받은 기업(융자한도 차감)\n- 지역신용보증재단신용보증기금기술보증기금의 보증금액 합계가 3억원 이상인 기업 또는 재단 보증금액 2억원 이상인 기업\n- 신청일 기준 현재 소유부동산에 대한 권리침해(압류가압류경매가처분 등)가 있는 기업\n- 최근 3개월 이내 30일 이상 연체가 있거나 10일 이상 연체가 4회 이상인 기업\n- 사치향락 등 보증제한업종 (별첨보증제한업종참조), 기타 보증제한사유에 해당하는 기업 (연체, 체납 등)\n- 그 외 재단 내규상 보증금지기업, 보증제한기업 등에 해당하는 기업\n\n⭐️ 우대사항\n\n\n👩 여성 대상\nX\n\n💁 청년 대상\nX\n\n⚠ 유의사항\n- 지원결정 후, 폐업, 관외이전, 최종 부도 처리된 기업 등\n- 허위 또는 기타 부정한 방법으로 융자지원 결정 또는 대출받은 경우\n- 기타 지원요건을 충족하지 못하여 사업추진이 어렵다고 판단될 경우\n- 매출액 대비 차입금 과다 등 기타 지원요건을 충족하지 못하여 사업 추진이 어렵다고 판단될 경우\n- 금융회사 내규에 따라 대출 취급이 거절될 경우\n\n📑 제출서류\n| 구비서류 | 비고 |\n

In [ ]:
test_data[0]